In [1]:
!pip install --quiet -r https://raw.githubusercontent.com/JoaquinLCalvo/Explained-CNN-SSL/refs/heads/explainability/requirements.txt

In [1]:
#Standard libraries
import os
from copy import deepcopy
from tqdm.notebook import tqdm

#plotting
import matplotlib.pyplot as plt
import seaborn as sns
sns.set()

#PyTorch
import pytorch_lightning as pl
import torch
import torch.nn as nn
import torch.nn.functional as F
import torch.optim as optim
from torch.utils.data import DataLoader, TensorDataset

#Torchvision
import torchvision
import torchvision.transforms.functional as FT
from torchvision import transforms
from torchvision.datasets import STL10

#PyTorch Lightning
from pytorch_lightning.callbacks import LearningRateMonitor
from pytorch_lightning.loggers import WandbLogger

#Explainability
from captum.attr import IntegratedGradients

#numpy
import numpy as np

#Wandb
import wandb

# Setting the seed
pl.seed_everything(47)

# Ensure that all operations are deterministic on GPU (if used) for reproducibility
torch.backends.cudnn.deterministic = True
torch.backends.cudnn.benchmark = False

# Path configurations
DATASET_PATH = "data/"
NUM_WORKERS = os.cpu_count()

# Device configs
device = torch.device("cuda:0") if torch.cuda.is_available() else torch.device("cpu")
print("Device:", device)
print("Number of workers:", NUM_WORKERS)

Seed set to 47


Device: cpu
Number of workers: 8


In [3]:
num_epochs = 25
batch_size = 256
lr = 1e-3
temperature = 0.07
hidden_dim = 128
weight_decay = 1e-4

In [ ]:
## Wandb Initialization

wandb.init(
    project="Explained-CNN-SimCLR",
    config={
        "name": "baseline_resnet18",
        "backbone": "resnet18",
        "epochs": num_epochs,
        "batch_size": batch_size,
        "learning_rate": lr,
        "weight_decay": weight_decay,
        "temperature": temperature,
        "hidden_dim": hidden_dim
    }
)

In [4]:
## Data Preparation

# To prepare the data loading we need to sample two different, random augmentations for each image in the batch.
# For this, we create a transformation that, when being called, applies a set of data augmentations to an image twice

class ContrastiveTransformations(object):

    def __init__(self, base_transforms, n_views=2):
        self.base_transforms = base_transforms
        self.n_views = n_views

    def __call__(self, x):
        return [self.base_transforms(x) for i in range(self.n_views)]

In [5]:
# Data augmentations for SimCLR

# Augmentation policy 1

contrast_transforms = transforms.Compose([
    transforms.RandomHorizontalFlip(),
    transforms.RandomResizedCrop(size=96),
    transforms.RandomApply([
        transforms.ColorJitter(brightness=0.5, contrast=0.5, saturation=0.5, hue=0.1)
    ], p=0.8),
    transforms.RandomGrayscale(p=0.2),
    transforms.GaussianBlur(kernel_size=9),
    transforms.ToTensor(),
    transforms.Normalize((0.5,), (0.5,))
])

# Augmentation policy 2

mixup_transforms = transforms.Compose([
   transforms.RandomHorizontalFlip(),
   transforms.RandomResizedCrop(size=96),
   transforms.RandomApply([
       transforms.ColorJitter(brightness=0.3, contrast=0.3, saturation=0.3)
   ], p=0.8),
   transforms.ToTensor(),
   transforms.Lambda(lambda img: mixup_augmentation(img)),  # Custom function for mixup
   transforms.Normalize((0.5,), (0.5,))
])

# Function to mix two images with a random alpha
def mixup_augmentation(img):
   alpha = 0.2  # Mixing factor
   lam = np.random.beta(alpha, alpha)
   mixed_img = lam * img + (1 - lam) * torch.flip(img, dims=[2])  # Simple example with flip
   return mixed_img

In [ ]:
# Datasets for contrastive learning
unlabeled_data = STL10(
    root=DATASET_PATH,
    split="unlabeled",
    download=True,
    transform=ContrastiveTransformations(contrast_transforms, n_views=2)
)

train_data_contrast = STL10(
    root=DATASET_PATH,
    split="train",
    download=True,
    transform=ContrastiveTransformations(mixup_transforms, n_views=2)
)

In [6]:
## SimCLR model definition

class SimCLR(pl.LightningModule):

    def __init__(self, hidden_dim, lr, temperature, weight_decay, max_epochs=500):
        super().__init__()
        self.save_hyperparameters()
        assert self.hparams.temperature > 0.0, 'The temperature must be a positive float!'
        # Base model f(.)
        self.convnet = torchvision.models.resnet18(num_classes=4*hidden_dim)  # Output of last linear layer
        # The MLP for g(.) consists of Linear->ReLU->Linear
        self.convnet.fc = nn.Sequential(
            self.convnet.fc,  # Linear(ResNet output, 4*hidden_dim)
            nn.ReLU(inplace=True),
            nn.Linear(4*hidden_dim, hidden_dim)
        )

    def configure_optimizers(self):
        optimizer = optim.AdamW(self.parameters(),
                                lr=self.hparams.lr,
                                weight_decay=self.hparams.weight_decay)
        lr_scheduler = optim.lr_scheduler.CosineAnnealingLR(optimizer,
                                                            T_max=self.hparams.max_epochs,
                                                            eta_min=self.hparams.lr/50)
        return [optimizer], [lr_scheduler]

    def info_nce_loss(self, batch, mode='train'):
        imgs, _ = batch
        imgs = torch.cat(imgs, dim=0)

        # Encode all images
        feats = self.convnet(imgs)
        # Calculate cosine similarity
        cos_sim = F.cosine_similarity(feats[:,None,:], feats[None,:,:], dim=-1)
        # Mask out cosine similarity to itself
        self_mask = torch.eye(cos_sim.shape[0], dtype=torch.bool, device=cos_sim.device)
        cos_sim.masked_fill_(self_mask, -9e15)
        # Find positive example -> batch_size//2 away from the original example
        pos_mask = self_mask.roll(shifts=cos_sim.shape[0]//2, dims=0)
        # InfoNCE loss
        cos_sim = cos_sim / self.hparams.temperature
        nll = -cos_sim[pos_mask] + torch.logsumexp(cos_sim, dim=-1)
        nll = nll.mean()

        # Logging loss
        self.log(mode+'_loss', nll)
        wandb.log({f"{mode}_loss": nll.item()})  # wandb logging

        # Get ranking position of positive example
        comb_sim = torch.cat([cos_sim[pos_mask][:,None],  # First position positive example
                              cos_sim.masked_fill(pos_mask, -9e15)],
                             dim=-1)
        sim_argsort = comb_sim.argsort(dim=-1, descending=True).argmin(dim=-1)

        # Calculate accuracy metrics
        top1_acc = (sim_argsort == 0).float().mean()
        top5_acc = (sim_argsort < 5).float().mean()
        mean_pos_acc = 1 + sim_argsort.float().mean()

        # Logging ranking metrics
        self.log(mode + '_acc_top1', top1_acc)
        self.log(mode + '_acc_top5', top5_acc)
        self.log(mode + '_acc_mean_pos', mean_pos_acc)

        wandb.log({
            f"{mode}_acc_top1": top1_acc.item(),
            f"{mode}_acc_top5": top5_acc.item(),
            f"{mode}_acc_mean_pos": mean_pos_acc.item()
        })

        return nll

    def training_step(self, batch, batch_idx):
        return self.info_nce_loss(batch, mode='train')

    def validation_step(self, batch, batch_idx):
        self.info_nce_loss(batch, mode='val')

In [ ]:
## Train SimCLR Model

def train_simclr(batch_size=batch_size, max_epochs=500, **kwargs):

    # Initialize the trainer
    trainer = pl.Trainer(
        accelerator="gpu" if str(device).startswith("cuda") else "cpu",
        devices=1,
        max_epochs=max_epochs,
        callbacks=[
            LearningRateMonitor(logging_interval='epoch')
        ]
    )

    trainer.logger._default_hp_metric = None

    # Create data loaders
    train_loader = DataLoader(
        unlabeled_data,
        batch_size=batch_size,
        shuffle=True,
        drop_last=True,
        pin_memory=True,
        num_workers=NUM_WORKERS
    )
    val_loader = DataLoader(
        train_data_contrast,
        batch_size=batch_size,
        shuffle=False,
        drop_last=False,
        pin_memory=True,
        num_workers=NUM_WORKERS
    )

    # Seed for reproducibility
    pl.seed_everything(47)

    # Initialize the SimCLR model
    model = SimCLR(max_epochs=max_epochs, **kwargs)

    # Train the model
    trainer.fit(model, train_loader, val_loader)

    return model


In [ ]:
# Train the SimCLR model
simclr_model = train_simclr(hidden_dim=hidden_dim,
                            lr=lr,
                            temperature=temperature,
                            weight_decay=weight_decay,
                            max_epochs=num_epochs)

In [7]:
# Downstream Classifier.
class LogisticRegression(pl.LightningModule):
    def __init__(self, feature_dim, num_classes, lr, weight_decay, max_epochs=500):
        super().__init__()
        self.save_hyperparameters()
        # Mapping from representation h to classes
        self.model = nn.Linear(feature_dim, num_classes)

    def configure_optimizers(self):
        optimizer = optim.AdamW(self.parameters(),
                                lr=self.hparams.lr,
                                weight_decay=self.hparams.weight_decay)
        lr_scheduler = optim.lr_scheduler.MultiStepLR(optimizer,
                                                      milestones=[int(self.hparams.max_epochs*0.6),
                                                                  int(self.hparams.max_epochs*0.8)],
                                                      gamma=0.1)
        return [optimizer], [lr_scheduler]

    def _calculate_loss(self, batch, mode='train'):
        feats, labels = batch
        preds = self.model(feats)
        loss = F.cross_entropy(preds, labels)
        acc = (preds.argmax(dim=-1) == labels).float().mean()

        self.log(mode + '_loss', loss)
        self.log(mode + '_acc', acc)
        return loss

    def training_step(self, batch, batch_idx):
        return self._calculate_loss(batch, mode='train')

    def validation_step(self, batch, batch_idx):
        self._calculate_loss(batch, mode='val')

    def test_step(self, batch, batch_idx):
        self._calculate_loss(batch, mode='test')

In [8]:
# Redefine the classifier but for the explainablity part

class LogisticRegressionForXai(LogisticRegression):
  def __init__(self, feature_dim, num_classes, simclr_model, lr, weight_decay, max_epochs=500):
        super().__init__(feature_dim=feature_dim, num_classes=num_classes, lr=lr, weight_decay=weight_decay)
        network = deepcopy(simclr_model.convnet)
        network.fc = nn.Identity()
        network.eval()
        self.simclr_model = network
        # Mapping from representation h to classes
        self.model = nn.Linear(feature_dim, num_classes)

  def configure_optimizers(self):
      optimizer = optim.AdamW(self.parameters(),
                              lr=self.hparams.lr,
                              weight_decay=self.hparams.weight_decay)
      lr_scheduler = optim.lr_scheduler.MultiStepLR(optimizer,
                                                    milestones=[int(self.hparams.max_epochs*0.6),
                                                                int(self.hparams.max_epochs*0.8)],
                                                    gamma=0.1)
      return [optimizer], [lr_scheduler]

  # function for the explainability call
  def forward(self, batch):
      images_features = []
      for img in batch:
          img = img.to(device)
          feats = self.simclr_model(img.unsqueeze(0))
          images_features.append(feats)
      images_features = torch.cat(images_features, dim=0)
      preds = self.model(images_features)
      return preds

In [9]:
# The training contains 500 images per class, while the test set has 800 images per class.

# Resize is not necessary since images are already 96x96
img_transforms = transforms.Compose([transforms.ToTensor(),
                                     transforms.Normalize((0.5,), (0.5,))])

train_img_data = STL10(root=DATASET_PATH, split='train', download=True,
                       transform=img_transforms)
test_img_data = STL10(root=DATASET_PATH, split='test', download=True,
                      transform=img_transforms)

print("Number of training examples:", len(train_img_data))
print("Number of test examples:", len(test_img_data))

Files already downloaded and verified
Files already downloaded and verified
Number of training examples: 5000
Number of test examples: 8000


In [10]:
SAVED_MODELS_PATH = "saved_models"
simclr_model_path = os.path.join(SAVED_MODELS_PATH, "simclr_model.pth")
simclr_logreg_model_contrast_path = os.path.join(SAVED_MODELS_PATH, "simclr_logreg_model_contrast.pth")
simclr_logreg_model_mixup_path = os.path.join(SAVED_MODELS_PATH, "simclr_logreg_model_mixup.pth")
resnet_model_contrast_path = os.path.join(SAVED_MODELS_PATH, "resnet_model_contrast.pth")
resnet_model_mixup_path = os.path.join(SAVED_MODELS_PATH, "resnet_model_mixup.pth")

In [11]:
simclr_model = SimCLR(
    hidden_dim=hidden_dim,
    lr=lr,
    temperature=temperature,
    weight_decay=weight_decay
)

state_dict = torch.load(simclr_model_path, weights_only=False)
filtered_state_dict = {k: v for k, v in state_dict.items() if not k.startswith('classifier.')}
simclr_model.load_state_dict(filtered_state_dict)

<All keys matched successfully>

In [12]:
# The function below creates a feature dataset by passing the original dataset (e.g., STL-10) through the SimCLR encoder
# This process generates fixed feature vectors (1D) for each image.

#  the encoder is modified to output features directly by replacing the projection head
# (g(.)) with an identity layer (nn.Identity).

# The extracted features are stored as a new TensorDataset

@torch.no_grad()
def prepare_data_features(model, dataset):
    # Prepare model
    network = deepcopy(model.convnet)
    network.fc = nn.Identity()  # Removing projection head g(.)
    network.eval()
    network.to(device)

    # Encode all images
    data_loader = DataLoader(dataset, batch_size=64, num_workers=NUM_WORKERS, shuffle=False, drop_last=False)
    feats, labels = [], []
    for batch_imgs, batch_labels in tqdm(data_loader):
        batch_imgs = batch_imgs.to(device)
        batch_feats = network(batch_imgs)
        feats.append(batch_feats.detach().cpu())
        labels.append(batch_labels)

    feats = torch.cat(feats, dim=0)
    labels = torch.cat(labels, dim=0)

    # Sort images by labels
    labels, idxs = labels.sort()
    feats = feats[idxs]

    return TensorDataset(feats, labels)

In [14]:
# Apply previous function to training and test sets.

train_feats_simclr = prepare_data_features(simclr_model, train_img_data)
test_feats_simclr = prepare_data_features(simclr_model, test_img_data)

  0%|          | 0/79 [00:00<?, ?it/s]

  0%|          | 0/125 [00:00<?, ?it/s]

In [29]:
# Training function
def train_logreg(batch_size, train_feats_data, test_feats_data, max_epochs=500, **kwargs):
    # Initialize wandb logger
    wandb_logger = WandbLogger(project="Explained-CNN-SimCLR")

    # Define the Trainer
    trainer = pl.Trainer(
        accelerator="gpu" if str(device).startswith("cuda") else "cpu",
        devices=1,
        max_epochs=max_epochs,
        logger=wandb_logger,
        callbacks=[LearningRateMonitor("epoch")],
        enable_progress_bar=True,
        check_val_every_n_epoch=1
    )
    trainer.logger._default_hp_metric = None  # Disable default metric tracking

    # Data loaders
    train_loader = DataLoader(
        train_feats_data, batch_size=batch_size, shuffle=True,
        drop_last=False, pin_memory=True, num_workers=0
    )
    test_loader = DataLoader(
        test_feats_data, batch_size=batch_size, shuffle=False,
        drop_last=False, pin_memory=True, num_workers=0
    )

    # Define LogisticRegression model
    class LogisticRegressionWithLogging(LogisticRegression):
        def training_step(self, batch, batch_idx):
            feats, labels = batch
            preds = self.model(feats)
            loss = F.cross_entropy(preds, labels)
            acc = (preds.argmax(dim=-1) == labels).float().mean()

            # Log training accuracy and loss
            self.log("train_loss", loss, prog_bar=True, on_epoch=True)
            self.log("train_accuracy", acc, prog_bar=True, on_epoch=True)
            wandb.log(
                {"train_loss": loss},
                {"train_accuracy": acc}
            )
            return loss

        def validation_step(self, batch, batch_idx):
            feats, labels = batch
            preds = self.model(feats)
            loss = F.cross_entropy(preds, labels)
            acc = (preds.argmax(dim=-1) == labels).float().mean()

            # Log validation accuracy
            self.log("val_loss", loss, prog_bar=True, on_epoch=True)
            self.log("val_accuracy", acc, prog_bar=True, on_epoch=True)
            wandb.log(
                {"val_loss": loss},
                {"val_accuracy": acc}
            )
            return loss

    # Instantiate the model
    model = LogisticRegressionWithLogging(**kwargs)

    # Train the model and log epoch-wise metrics
    trainer.fit(model, train_dataloaders=train_loader, val_dataloaders=test_loader)

    # Test the model for final accuracy results
    train_result = trainer.test(model, train_loader, verbose=False)
    test_result = trainer.test(model, test_loader, verbose=False)

    # Log final train and test accuracy to wandb
    wandb.log({
        "final_train_accuracy": train_result[0]["test_acc"],
        "final_test_accuracy": test_result[0]["test_acc"]
    })

    # Finish wandb run
    wandb.finish()

    return model, {"train_accuracy": train_result[0]["test_acc"], "test_accuracy": test_result[0]["test_acc"]}


In [ ]:
# Train and evaluate
results = {}

# Train logistic regression with the full training dataset
logreg_model, full_set_results = train_logreg(
    batch_size=64,
    train_feats_data=train_feats_simclr,
    test_feats_data=test_feats_simclr,
    feature_dim=train_feats_simclr.tensors[0].shape[1],  # Feature size from SimCLR
    num_classes=10,
    lr=lr,
    weight_decay=weight_decay
)

# Store the results
results["full_dataset"] = full_set_results


In [ ]:
# Print results
print(f"Train accuracy: {results['full_dataset']['train_accuracy'] * 100:.2f}%")
print(f"Test accuracy: {results['full_dataset']['test_accuracy'] * 100:.2f}%")

In [ ]:
## Save the model
# Path to save the model on Colab
simclr_logreg_model_save_path = "simclr_logreg_model.pth"

# Save the model's state_dict
torch.save(logreg_model.state_dict(), simclr_logreg_model_save_path)
print(f"Model saved to {simclr_logreg_model_save_path}")

# Download the model to your local machine
from google.colab import files
files.download(simclr_logreg_model_save_path)

In [15]:
simclr_logreg_model = LogisticRegressionForXai(
    lr=lr,
    weight_decay=weight_decay,
    feature_dim=train_feats_simclr.tensors[0].shape[1],
    num_classes=10,
    simclr_model=simclr_model
)
simclr_logreg_model.load_state_dict(torch.load(simclr_logreg_model_contrast_path, weights_only=True), strict=False)
simclr_logreg_model.eval()

/home/leo/uni/ml_for_NLP/practical/Explained-CNN-SSL/env/lib/python3.12/site-packages/pytorch_lightning/utilities/parsing.py:209: Attribute 'simclr_model' is an instance of `nn.Module` and is already saved during checkpointing. It is recommended to ignore them using `self.save_hyperparameters(ignore=['simclr_model'])`.


LogisticRegressionForXai(
  (model): Linear(in_features=512, out_features=10, bias=True)
  (simclr_model): ResNet(
    (conv1): Conv2d(3, 64, kernel_size=(7, 7), stride=(2, 2), padding=(3, 3), bias=False)
    (bn1): BatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
    (relu): ReLU(inplace=True)
    (maxpool): MaxPool2d(kernel_size=3, stride=2, padding=1, dilation=1, ceil_mode=False)
    (layer1): Sequential(
      (0): BasicBlock(
        (conv1): Conv2d(64, 64, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1), bias=False)
        (bn1): BatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
        (relu): ReLU(inplace=True)
        (conv2): Conv2d(64, 64, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1), bias=False)
        (bn2): BatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
      )
      (1): BasicBlock(
        (conv1): Conv2d(64, 64, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1), bias=

In [16]:
class ResNet(pl.LightningModule):
    def __init__(self, num_classes, lr, weight_decay, max_epochs=100):
        super().__init__()
        self.save_hyperparameters()
        self.model = torchvision.models.resnet18(pretrained=False, num_classes=num_classes)

    def configure_optimizers(self):
        optimizer = optim.AdamW(self.parameters(),
                                lr=self.hparams.lr,
                                weight_decay=self.hparams.weight_decay)
        lr_scheduler = optim.lr_scheduler.CosineAnnealingLR(optimizer,
                                                            T_max=self.hparams.max_epochs,
                                                            eta_min=self.hparams.lr/50)
        return [optimizer], [lr_scheduler]

    def _calculate_loss(self, batch, mode="train"):
        imgs, labels = batch
        preds = self.model(imgs)
        loss = F.cross_entropy(preds, labels)
        acc = (preds.argmax(dim=-1) == labels).float().mean()

        self.log(mode + "_loss", loss)
        self.log(mode + "_acc", acc)
        wandb.log(
            {f"{mode}_loss": loss},
            {f"{mode}_acc": acc}
        ) 
        return loss

    def training_step(self, batch, batch_idx):
        return self._calculate_loss(batch, mode="train")

    def validation_step(self, batch, batch_idx):
        self._calculate_loss(batch, mode="val")

    def test_step(self, batch, batch_idx):
        self._calculate_loss(batch, mode="test")

In [22]:
# Train ResNet-18 Model

def train_resnet18(train_dataset, val_dataset, batch_size=batch_size, max_epochs=500, lr=lr, weight_decay=weight_decay, num_classes=10, **kwargs):

    # Initialize the trainer
    trainer = pl.Trainer(
        accelerator="gpu" if str(device).startswith("cuda") else "cpu",
        devices=1,
        max_epochs=max_epochs,
        callbacks=[
            LearningRateMonitor(logging_interval='epoch')
        ]
    )

    trainer.logger._default_hp_metric = None

    # Create data loaders
    train_loader = DataLoader(
        train_dataset,
        batch_size=batch_size,
        shuffle=True,
        drop_last=True,
        pin_memory=True,
        num_workers=NUM_WORKERS
    )
    val_loader = DataLoader(
        val_dataset,
        batch_size=batch_size,
        shuffle=False,
        drop_last=False,
        pin_memory=True,
        num_workers=NUM_WORKERS
    )

    # Seed for reproducibility
    pl.seed_everything(47)

    # Initialize the ResNet-18 model
    model = ResNet(
        lr=lr,
        weight_decay=weight_decay,
        num_classes=num_classes,
    )

    # Train the model
    trainer.fit(model, train_loader, val_loader)

    wandb.finish()

    return model


In [17]:
# ResNet-18 class for explainability with forward function

class ResNetForXai(ResNet):
    def __init__(self, num_classes, lr, weight_decay, max_epochs=500):
        super().__init__(num_classes=num_classes, lr=lr, weight_decay=weight_decay)
    
    def forward(self, batch):
        return self.model(batch)

In [56]:
# Train ResNet-18

train_dataset = STL10(
    root=DATASET_PATH,
    split="train",
    download=True,
    transform=mixup_transforms
)

val_dataset = STL10(
    root=DATASET_PATH, 
    split='test',
    download=True,
    transform=transforms.Compose(
        [
            transforms.ToTensor(),
            transforms.Normalize((0.5,), (0.5,))
        ]
    )
)

resnet_model = train_resnet18(
    train_dataset=train_dataset,
    val_dataset=val_dataset,
    batch_size=batch_size,
    max_epochs=num_epochs,
    lr=lr,
    weight_decay=weight_decay,
    num_classes=10
)

In [18]:
# Load the model

resnet_model_for_xai = ResNetForXai(
    lr=lr,
    weight_decay=weight_decay,
    num_classes=10,
)
# resnet_model_for_xai.load_state_dict(resnet_model.state_dict())
resnet_model_for_xai.load_state_dict(torch.load(resnet_model_contrast_path, weights_only=True))
resnet_model_for_xai.eval()

/home/leo/uni/ml_for_NLP/practical/Explained-CNN-SSL/env/lib/python3.12/site-packages/torchvision/models/_utils.py:208: UserWarning: The parameter 'pretrained' is deprecated since 0.13 and may be removed in the future, please use 'weights' instead.
  warnings.warn(
/home/leo/uni/ml_for_NLP/practical/Explained-CNN-SSL/env/lib/python3.12/site-packages/torchvision/models/_utils.py:223: UserWarning: Arguments other than a weight enum or `None` for 'weights' are deprecated since 0.13 and may be removed in the future. The current behavior is equivalent to passing `weights=None`.
  warnings.warn(msg)


ResNetForXai(
  (model): ResNet(
    (conv1): Conv2d(3, 64, kernel_size=(7, 7), stride=(2, 2), padding=(3, 3), bias=False)
    (bn1): BatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
    (relu): ReLU(inplace=True)
    (maxpool): MaxPool2d(kernel_size=3, stride=2, padding=1, dilation=1, ceil_mode=False)
    (layer1): Sequential(
      (0): BasicBlock(
        (conv1): Conv2d(64, 64, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1), bias=False)
        (bn1): BatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
        (relu): ReLU(inplace=True)
        (conv2): Conv2d(64, 64, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1), bias=False)
        (bn2): BatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
      )
      (1): BasicBlock(
        (conv1): Conv2d(64, 64, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1), bias=False)
        (bn1): BatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True, track_

In [27]:
# Setting some variables

EXAMPLES_FOLDER = "examples"
EXAMPLE_NUMBER = "ig_gaussian_baseline_contrast"
examples_image_folder_path = os.path.join(EXAMPLES_FOLDER, EXAMPLE_NUMBER)
os.makedirs(examples_image_folder_path, exist_ok=True)

EXAMPLE_IMAGE_NAME = "gaussian_baseline_contrast_attributions.png"
examples_image_path = os.path.join(examples_image_folder_path, EXAMPLE_IMAGE_NAME)

EXAMPLES_COUNT = 5
class_names = ["airplane", "bird", "car", "cat", "deer", "dog", "horse", "monkey", "ship", "truck"]
models = {
    'simclr': simclr_logreg_model,
    'resnet': resnet_model_for_xai
}

In [20]:
# Getting some example images from the dataset
def get_examples(size=EXAMPLES_COUNT):
    examples = []
    for i in range(size):
        image, label = test_img_data[i]
        examples.append({
            'img': image,
            'label': label
        })
    return examples

In [26]:
examples = get_examples()

In [28]:
def get_attributions(model, examples: list):

    def forward_fn(inputs):
        if inputs.dim() == 3:
            inputs = inputs.unsqueeze(0)
        return model(inputs)

    method = IntegratedGradients(forward_fn)

    results = []
    for example in examples:
        input_tensor = example['img']
        input_tensor = input_tensor.unsqueeze(0)

        with torch.no_grad():
            logits = model(input_tensor)
            target_class = logits.argmax(dim=-1).item()
        
        gaussian_blur = transforms.GaussianBlur(kernel_size=13, sigma=2)
        baseline_image = gaussian_blur(input_tensor)

        attributions = method.attribute(
            inputs=input_tensor, target=target_class,
            baselines=baseline_image
            # baselines=torch.zeros_like(input_tensor)
        )
        attributions_np = attributions[0].cpu().detach().numpy()
        attributions_np = (attributions_np - attributions_np.min()) / (attributions_np.max() - attributions_np.min())

        if attributions_np.ndim == 3:
            attributions_np = attributions_np.transpose(1, 2, 0)
        results.append({
            'prediction': target_class,
            'attr': attributions_np
        })
    return results

In [29]:
models_attributions = {}
for model_name in models:
    models_attributions[model_name] = get_attributions(model=models[model_name], examples=examples)
    for idx in range(len(examples)):
        examples[idx][model_name] = {}
        examples[idx][model_name]['prediction'] = models_attributions[model_name][idx]['prediction']
        examples[idx][model_name]['attr'] = models_attributions[model_name][idx]['attr']

In [30]:
def show_attributions(attributions, model_names, save_fig=False):
    if not isinstance(attributions, list):
        attributions = [attributions]
    fig, ax = plt.subplots(len(attributions), len(model_names) + 1, figsize=(12, 5 * len(attributions)))
    for idx, ex in enumerate(attributions):
        img = ex['img']
        label = ex['label']

        img = img.detach()
        img = FT.to_pil_image(img)

        ax[idx, 0].imshow(np.asarray(img))
        ax[idx, 0].set_title(f'Original image class is {class_names[label]}')

        for jdx, model_name in enumerate(model_names):
            prediction = ex[model_name]['prediction']
            attr = ex[model_name]['attr']
            ax[idx, jdx + 1].imshow(attr)
            ax[idx, jdx + 1].set_title(f'Attributions of {model_name} (predicted: {class_names[prediction]})')
    plt.tight_layout()
    if save_fig:
        plt.savefig(examples_image_path)
    plt.show()

In [31]:
show_attributions(attributions=examples, model_names=models.keys(), save_fig=True)